In [1]:
import os
import pandas as pd
import numpy as np
import matplotlib
import matplotlib.pyplot as plt
import matplotlib.ticker as ticker
from mpl_toolkits.axes_grid1 import make_axes_locatable
from matplotlib.colors import LinearSegmentedColormap
import re
import unicodedata
# %matplotlib inline

In [2]:
pd.set_option('display.max_columns',200)
pd.set_option('display.max_rows',200)
global color_h, color_f, color_b, PLOTDIM, FREQYEARS
color_h = "gold"
color_f = "royalblue"
color_b = "lightgray"
PLOTDIM = (9,6)
FREQYEARS = 10

## Chargement des données

In [3]:
# Les données sont stockées dans le dossier "data", c'est plus clean
authors  = pd.read_csv('../data/ALL_AUTHORS (live_work + clean nat).csv',sep=',', low_memory=False)
art = pd.read_csv('../data/ALL_ARTWORKS.csv',low_memory=False)
art = art[~pd.isnull(art['acquisition_year'])]

## Transformation des données

#### Changement des mauvais noms de collec

In [4]:
# Transform bad collections
art.loc[art['collection'] == "Musée national d'art moderne / Centre de cr��ation industrielle", 'collection'] = "Musée national d'art moderne / Centre de création industrielle"
art.loc[art['collection'] == "Mus��e d'Art moderne et contemporain de la Ville de Strasbourg", 'collection'] = "Musée d'Art moderne et contemporain de la Ville de Strasbourg"
art.loc[art['collection'] == "Mus��e national d'art moderne / Centre de création industrielle", 'collection'] = "Musée national d'art moderne / Centre de création industrielle"
art.loc[art['collection'] == "La Piscine, Mus��e d'art et d'industrie André Diligent, Roubaix", 'collection'] = "La Piscine, Musée d'art et d'industrie André Diligent, Roubaix"
art.loc[art['collection'] == "Mus��e d'art contemporain de Lyon", 'collection'] = "Musée d'art contemporain de Lyon"
#print(art['collection'].value_counts())
print(len(art['collection'].unique()))

59


#### Ajout d'un genre aux oeuvres

In [5]:
art['Gender'] = None
counter = 0
done = 0
length = len(art)
done_percentage = 0

for _,i in art.iterrows():
    counter += 1
    if pd.isnull(i['authors']) == False:
        c = re.split(r'\|', i['authors'])#split
        # If several authors: we see if they all have same gender, else "groupe"
        if len(c) > 1:
            gender_list = [authors[authors['Id artist'] == int(b)]['Gender'].values[0] for b in c]
            if all("masculin" == g for g in gender_list):
                var = "masculin"
            elif all("féminin" == g for g in gender_list):
                var = "féminin"
            else:
                var = "groupe"
        # If one author: trivial
        else:
            b = c[0]
            var = authors[authors['Id artist'] == int(b)]['Gender'].values[0]

        art.at[_,'Gender'] = var
        done += 1
    
    if counter % 10000==0:
        print(f'percentage: {round(100*counter/length, 3)}%, total = {counter}')
        # print(i['Gender'])

percentage: 2.871%, total = 10000
percentage: 5.742%, total = 20000
percentage: 8.612%, total = 30000
percentage: 11.483%, total = 40000
percentage: 14.354%, total = 50000
percentage: 17.225%, total = 60000
percentage: 20.096%, total = 70000
percentage: 22.967%, total = 80000
percentage: 25.837%, total = 90000
percentage: 28.708%, total = 100000
percentage: 31.579%, total = 110000
percentage: 34.45%, total = 120000
percentage: 37.321%, total = 130000
percentage: 40.192%, total = 140000
percentage: 43.062%, total = 150000
percentage: 45.933%, total = 160000
percentage: 48.804%, total = 170000
percentage: 51.675%, total = 180000
percentage: 54.546%, total = 190000
percentage: 57.416%, total = 200000
percentage: 60.287%, total = 210000
percentage: 63.158%, total = 220000
percentage: 66.029%, total = 230000
percentage: 68.9%, total = 240000
percentage: 71.771%, total = 250000
percentage: 74.641%, total = 260000
percentage: 77.512%, total = 270000
percentage: 80.383%, total = 280000
percent

#### Ajout d'un age

In [6]:
# Computing age at acquisition
art['age_at_acquisition'] = None
counter = 0
done = 0
length = len(art)
done_percentage = 0

for _,i in art.iterrows():
    counter += 1
    if pd.isnull(i['authors']) == False:
        c = re.split(r'\|', i['authors'])#split
        # If several authors: we take the average age
        if len(c) > 1:
            ages_list = [authors[authors['Id artist'] == int(b)]['Birth year'].values[0] for b in c]
            var = i['acquisition_year'] - np.nanmean(ages_list)
        # If one author: trivial
        else:
            b = c[0]
            var = i['acquisition_year'] - authors[authors['Id artist'] == int(b)]['Birth year'].values[0]

        art.at[_,'age_at_acquisition'] = var
        done += 1
    
    if counter % 10000==0:
        print(f'percentage: {round(100*counter/length, 3)}%, total = {counter}')

art['age_at_acquisition'] = pd.to_numeric(art['age_at_acquisition'])
art['age_at_acquisition'].count()/len(art) #18% de NaN

c:\program files\python36\lib\site-packages\ipykernel_launcher.py:15: RuntimeWarning: Mean of empty slice
  from ipykernel import kernelapp as app


percentage: 2.871%, total = 10000
percentage: 5.742%, total = 20000
percentage: 8.612%, total = 30000
percentage: 11.483%, total = 40000
percentage: 14.354%, total = 50000
percentage: 17.225%, total = 60000
percentage: 20.096%, total = 70000
percentage: 22.967%, total = 80000
percentage: 25.837%, total = 90000
percentage: 28.708%, total = 100000
percentage: 31.579%, total = 110000
percentage: 34.45%, total = 120000
percentage: 37.321%, total = 130000
percentage: 40.192%, total = 140000
percentage: 43.062%, total = 150000
percentage: 45.933%, total = 160000
percentage: 48.804%, total = 170000
percentage: 51.675%, total = 180000
percentage: 54.546%, total = 190000
percentage: 57.416%, total = 200000
percentage: 60.287%, total = 210000
percentage: 63.158%, total = 220000
percentage: 66.029%, total = 230000
percentage: 68.9%, total = 240000
percentage: 71.771%, total = 250000
percentage: 74.641%, total = 260000
percentage: 77.512%, total = 270000
percentage: 80.383%, total = 280000
percent

0.89094025240288

#### Ajout d'une nationalité

In [7]:
art['nationality'] = None
counter = 0
done = 0
length = len(art)
done_percentage = 0

for _,i in art.iterrows():
    counter += 1
    if pd.isnull(i['authors']) == False:
        c = re.split(r'\|', i['authors'])#split
        # If several authors: we see if they all have same gender, else "groupe"
        if len(c) > 1:
           # nat_list = [authors[authors['Id artist'] == int(b)]['nationality_clean'].values[0] for b in c if ]
            nat_list = []
            for b in c:
                if pd.notnull(authors[authors['Id artist'] == int(b)]['nationality_clean'].values[0]):
                    nat_list.append(authors[authors['Id artist'] == int(b)]['nationality_clean'].values[0])
            if any("français" in g for g in nat_list):
                var = "français"
            else:
                var = "groupe"
        # If one author: trivial
        else:
            b = c[0]
            var = authors[authors['Id artist'] == int(b)]['nationality_clean'].values[0]

        art.at[_,'nationality'] = var
        done += 1
    
    if counter % 10000==0:
        print(f'percentage: {round(100*counter/length, 3)}%, total = {counter}')

percentage: 2.871%, total = 10000
percentage: 5.742%, total = 20000
percentage: 8.612%, total = 30000
percentage: 11.483%, total = 40000
percentage: 14.354%, total = 50000
percentage: 17.225%, total = 60000
percentage: 20.096%, total = 70000
percentage: 22.967%, total = 80000
percentage: 25.837%, total = 90000
percentage: 28.708%, total = 100000
percentage: 31.579%, total = 110000
percentage: 34.45%, total = 120000
percentage: 37.321%, total = 130000
percentage: 40.192%, total = 140000
percentage: 43.062%, total = 150000
percentage: 45.933%, total = 160000
percentage: 48.804%, total = 170000
percentage: 51.675%, total = 180000
percentage: 54.546%, total = 190000
percentage: 57.416%, total = 200000
percentage: 60.287%, total = 210000
percentage: 63.158%, total = 220000
percentage: 66.029%, total = 230000
percentage: 68.9%, total = 240000
percentage: 71.771%, total = 250000
percentage: 74.641%, total = 260000
percentage: 77.512%, total = 270000
percentage: 80.383%, total = 280000
percent

### Ajout de la primauté de l'oeuvre

In [8]:
l = len(authors) - 1
authors['acquisition_date_clean'] = None
for i, author in authors.iterrows():
    arts = author['ID artworks']
    dates = []
    if not pd.isnull(arts):
        arts = re.split(r'\|', arts)
        for id_art in arts:
            artwork = art[art['_id'] == int(id_art)]
            if not artwork.empty:
                if not pd.isnull(artwork['acquisition_year'].values[0]):
                    dates.append(str(int(artwork['acquisition_year'].values[0])))
    if len(dates) > 0:
        dates = '|'.join(dates)
        authors.at[i, 'acquisition_date_clean'] = dates
    if i % 10000 == 0:
        print("Percentage:", int(i/l * 100), "total:", i)

Percentage: 0 total: 0
Percentage: 27 total: 10000
Percentage: 55 total: 20000
Percentage: 83 total: 30000


In [9]:
art['is_first'] = 0
l = len(art)

for i, artwork in art.iterrows():
    date = artwork['acquisition_year']
    isfirst = 0
    if not pd.isnull(artwork['authors']):
        c = re.split(r'\|', artwork['authors'])
        for b in c:
            aut = authors[authors['Id artist'] == int(b)]
            # print(aut['acquisition_date_clean'].values[0])
            all_acqu = re.split(r'\|', aut['acquisition_date_clean'].values[0])
            print(date)
            isfirst += int(int(date) == int(min(all_acqu)))                
        
        art.at[i,'is_first'] = int(isfirst > 0)
    
    if i % 10000 == 0:
        print("Percentage:", int(i/l * 100), "total:", i)

1996.0
Percentage: 0 total: 0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996

1979.0
1971.0
1971.0
1970.0
1968.0
1979.0
1971.0
1970.0
1970.0
1987.0
1987.0
1984.0
1984.0
1984.0
1984.0
1997.0
1975.0
1975.0
1977.0
1985.0
1859.0
1860.0
1946.0
1877.0
1880.0
1924.0
1889.0
1889.0
1954.0
2017.0
2017.0
2017.0
2017.0
2017.0
2017.0
1983.0
1953.0
1955.0
1883.0
1883.0
1883.0
1883.0
1883.0
1967.0
1976.0
1985.0
1954.0
1954.0
1922.0
1938.0
1916.0
1917.0
1924.0
1925.0
1842.0
1852.0
1959.0
1963.0
1966.0
1948.0
1951.0
1934.0
1934.0
1981.0
1967.0
1967.0
1971.0
1854.0
1854.0
1854.0
1854.0
1928.0
1928.0
1919.0
1919.0
1919.0
1919.0
1919.0
1919.0
1919.0
1919.0
1919.0
1919.0
1919.0
1919.0
1919.0
1919.0
1919.0
1919.0
1919.0
1919.0
1919.0
1919.0
1921.0
1921.0
1921.0
1921.0
1921.0
1921.0
1921.0
1921.0
1921.0
1919.0
1919.0
1928.0
1848.0
1954.0
1954.0
1963.0
1963.0
1921.0
1923.0
1923.0
1938.0
1902.0
1902.0
1902.0
1902.0
1902.0
1885.0
1891.0
1902.0
1885.0
1876.0
1879.0
1890.0
1893.0
1902.0
1902.0
1902.0
1881.0
1894.0
1891.0
1889.0
1888.0
1881.0
1891.0
1893.0
1906.0
1907.0
1908.0
1910.0
1887.0

1970.0
1970.0
1975.0
1989.0
1989.0
1989.0
1989.0
1989.0
1989.0
2011.0
1956.0
1954.0
1977.0
1959.0
1935.0
1942.0
1964.0
1936.0
1938.0
1938.0
1938.0
1942.0
1943.0
1967.0
1946.0
1947.0
1943.0
1943.0
1943.0
1947.0
1947.0
1947.0
1964.0
1971.0
1975.0
1982.0
1974.0
1978.0
1984.0
1984.0
1996.0
2018.0
2012.0
2012.0
2015.0
1986.0
1988.0
1988.0
1988.0
1986.0
1988.0
1988.0
1988.0
1986.0
1988.0
1988.0
1988.0
1981.0
1979.0
2012.0
2012.0
2011.0
1984.0
1984.0
1985.0
1985.0
1985.0
1989.0
1989.0
1986.0
1987.0
1987.0
1987.0
1989.0
1989.0
1988.0
1989.0
1989.0
1989.0
1989.0
1989.0
1994.0
1995.0
1989.0
1991.0
2002.0
1993.0
1996.0
1953.0
1957.0
1935.0
1988.0
1953.0
1959.0
1976.0
1957.0
1959.0
1971.0
1974.0
1984.0
1957.0
1959.0
1964.0
1968.0
2011.0
2009.0
2009.0
2009.0
2000.0
2005.0
1979.0
1983.0
1974.0
1980.0
1975.0
1974.0
1975.0
1974.0
1975.0
1976.0
1983.0
1984.0
1982.0
1979.0
1980.0
1981.0
1981.0
1989.0
1986.0
1983.0
1984.0
1984.0
2009.0
2009.0
2009.0
2009.0
2009.0
2009.0
2009.0
2009.0
2009.0
2009.0
2009.0

1847.0
1864.0
1865.0
1869.0
2016.0
2016.0
2016.0
2016.0
2016.0
2016.0
2016.0
2016.0
2016.0
2016.0
2016.0
2016.0
1991.0
1994.0
2008.0
2010.0
2015.0
1983.0
1983.0
1983.0
1983.0
1983.0
1983.0
1983.0
1983.0
1983.0
2005.0
2005.0
2005.0
1987.0
2004.0
2004.0
2004.0
2004.0
2004.0
2004.0
2007.0
2007.0
2007.0
2007.0
2007.0
2007.0
2007.0
2014.0
1939.0
1945.0
1952.0
1859.0
1853.0
1842.0
1852.0
1856.0
1849.0
1843.0
1847.0
1855.0
1858.0
1870.0
1955.0
1955.0
1955.0
1955.0
1955.0
1955.0
1910.0
1920.0
1921.0
1922.0
1922.0
1922.0
1923.0
1923.0
1923.0
1923.0
1923.0
1911.0
1922.0
1922.0
1909.0
1910.0
1912.0
1912.0
1922.0
1924.0
1985.0
2010.0
2010.0
2010.0
2010.0
2010.0
2010.0
2010.0
2010.0
2010.0
2010.0
1933.0
1932.0
1926.0
1932.0
1950.0
1957.0
1952.0
1952.0
1952.0
1953.0
1955.0
1961.0
1988.0
1913.0
1925.0
1883.0
1881.0
1887.0
1888.0
1887.0
1892.0
1894.0
1896.0
1897.0
1901.0
1906.0
1912.0
1901.0
1904.0
1919.0
1895.0
1895.0
1895.0
1895.0
1893.0
1893.0
1895.0
1895.0
2010.0
2010.0
1928.0
1930.0
1934.0
1936.0

1916.0
1919.0
1917.0
1912.0
1912.0
2013.0
2013.0
1928.0
1982.0
1952.0
1955.0
1958.0
1979.0
1973.0
1939.0
1939.0
1940.0
1941.0
1944.0
1944.0
1944.0
1950.0
1952.0
1955.0
1955.0
1957.0
1961.0
1963.0
1925.0
1932.0
1939.0
1941.0
1941.0
1942.0
1942.0
1944.0
1945.0
1948.0
1950.0
1951.0
1952.0
1954.0
1955.0
1957.0
1947.0
1936.0
1955.0
1955.0
1932.0
1944.0
1955.0
1934.0
1934.0
1955.0
1940.0
1949.0
1977.0
1953.0
1954.0
1956.0
1956.0
1957.0
1959.0
1960.0
1961.0
1961.0
1992.0
1992.0
1860.0
1959.0
1937.0
1910.0
1860.0
1973.0
1983.0
2012.0
1991.0
1991.0
1933.0
1978.0
1963.0
1842.0
1843.0
1912.0
1908.0
1913.0
1918.0
1920.0
1928.0
1906.0
1934.0
1920.0
1922.0
1966.0
1954.0
1957.0
2017.0
2017.0
1946.0
1937.0
1918.0
1922.0
1930.0
1927.0
2013.0
2013.0
2013.0
2013.0
2013.0
2013.0
2013.0
2000.0
1953.0
1924.0
1926.0
2011.0
2011.0
1993.0
1993.0
1993.0
1993.0
1993.0
1993.0
2006.0
2006.0
2006.0
2006.0
2006.0
1991.0
1991.0
2006.0
1994.0
1993.0
1994.0
1994.0
1993.0
1994.0
1994.0
1994.0
1994.0
2003.0
2003.0
2003.0

...

2001.0
2001.0
2001.0
2001.0
2001.0
2001.0
1991.0
1991.0
1991.0
1991.0
1991.0
2005.0
2005.0
2005.0
1991.0
1991.0
1991.0
1991.0
1991.0
1991.0
1991.0
1991.0
1991.0
2001.0
2001.0
2001.0
2001.0
2001.0
2001.0
1991.0
1991.0
1991.0
1991.0
1991.0
1991.0
1991.0
1991.0
1991.0
1991.0
1991.0
1991.0
2005.0
1991.0
1991.0
1991.0
1991.0
1991.0
2001.0
2001.0
2001.0
2001.0
2001.0
2001.0
2001.0
2001.0
2001.0
1991.0
1991.0
1991.0
1991.0
1991.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
1991.0
1991.0
1991.0
1991.0
1991.0
1991.0
1991.0
2001.0
2001.0
2001.0
2001.0
2001.0
2001.0
2001.0
2001.0
2001.0
2001.0
1987.0
1991.0
1991.0
1991.0
1991.0
1991.0
1991.0
2005.0
2005.0
2005.0
1991.0
1991.0
1991.0
1991.0
1991.0
1991.0
1991.0
1991.0
1983.0
1983.0
1983.0
1985.0
2001.0
2001.0
2001.0
2001.0
2001.0
2001.0
2001.0
2001.0
2001.0
2001.0
2001.0
2001.0
2001.0
2001.0
2001.0
1991.0
1991.0
1991.0
1991.0
1991.0
1991.0
2001.0
2001.0
2001.0
2001.0
2001.0
2001.0
2001.0
2001.0
2001.0

1945.0
1945.0
1945.0
1949.0
1949.0
1955.0
1949.0
1959.0
1962.0
1962.0
1864.0
1866.0
1997.0
1997.0
2009.0
1997.0
1997.0
2005.0
2009.0
1906.0
1955.0
1957.0
1965.0
1980.0
1982.0
1837.0
1987.0
2007.0
2002.0
1931.0
1930.0
1984.0
1987.0
1988.0
1988.0
1988.0
1989.0
1989.0
2006.0
1997.0
1961.0
1961.0
1973.0
1960.0
1952.0
1967.0
1962.0
1966.0
1966.0
1967.0
1967.0
1967.0
1970.0
2001.0
2005.0
1955.0
1962.0
1963.0
1969.0
1959.0
1961.0
1932.0
1935.0
1935.0
1936.0
1938.0
1944.0
1909.0
1942.0
1973.0
1987.0
1980.0
1982.0
1983.0
1989.0
1989.0
1987.0
1987.0
1991.0
1996.0
2011.0
2011.0
2011.0
2011.0
2011.0
2011.0
2011.0
2008.0
2011.0
1933.0
1920.0
1911.0
1878.0
1871.0
1877.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0
1999.0

2000.0
2000.0
2000.0
2004.0
2004.0
1995.0
1996.0
1997.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
1995.0
1998.0
1997.0
1998.0
1997.0
1997.0
2012.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
1998.0
1999.0
2000.0
2000.0
2000.0
2000.0
2000.0
2000.0
2012.0
2000.0
2008.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2010.0
2000.0
2000.0
2006.0
2007.0
2003.0
2002.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2010.0
2000.0
2000.0
2000.0
2000.0
2000.0
2000.0
2000.0
2012.0
2012.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0
2003.0

1966.0
1966.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2011.0
1963.0
1957.0
1966.0
1966.0
1966.0
1966.0
1966.0
1966.0
1966.0
1966.0
1966.0
1966.0
1966.0
1966.0
1966.0
1966.0
1966.0
1966.0
1966.0
1996.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0
2005.0

1992.0
1992.0
1995.0
2003.0
2003.0
2003.0
2003.0
2003.0
2006.0
1988.0
1996.0
1988.0
1987.0
2010.0
1996.0
1992.0
1992.0
1990.0
1990.0
1992.0
1992.0
1992.0
1990.0
1991.0
1995.0
1992.0
1992.0
1992.0
2010.0
1992.0
1999.0
1992.0
1996.0
1996.0
1996.0
1996.0
1995.0
1995.0
1995.0
1996.0
1996.0
1996.0
1993.0
1995.0
2017.0
1996.0
1996.0
1996.0
1996.0
1996.0
1996.0
1995.0
2006.0
2003.0
2010.0
2010.0
2010.0
2010.0
2010.0
2010.0
2010.0
2010.0
2010.0
2010.0
2010.0
2010.0
2010.0
2004.0
2004.0
2004.0
2006.0
1994.0
2004.0
2010.0
2010.0
2010.0
2010.0
2010.0
2012.0
1986.0
1987.0
1989.0
1990.0
2003.0
1992.0
1993.0
2003.0
2006.0
1996.0
2001.0
2009.0
1992.0
1985.0
1989.0
2009.0
1997.0
1997.0
2004.0
1959.0
1949.0
1951.0
1952.0
1947.0
1950.0
1952.0
1955.0
1956.0
1957.0
1970.0
1963.0
1963.0
1963.0
1963.0
1963.0
1953.0
1955.0
1959.0
1960.0
1964.0
1975.0
1957.0
1957.0
1958.0
1959.0
1961.0
1951.0
1951.0
1953.0
1953.0
1953.0
1953.0
1953.0
1953.0
1953.0
1955.0
1958.0
1963.0
1963.0
1963.0
1969.0
1949.0
1970.0
1940.0

In [10]:
sum(art['is_first'])

81138

#### Sauvegarde des modifs

In [11]:
art.to_csv("../data/ALL_ARTWORKS (for stats use ONLY).csv", sep=',', encoding='utf-8', index=False)